In [1]:
import geopandas as gpd
from datetime import datetime
from libcomcat.search import search
import pandas as pd
import pprint

# Import

In [2]:

# =============================================================================
# =============================================================================

# --- 1. Paramètres utilisateur ---
geojson_path = "myanmar.json"    # <- à adapter
date_start = "2025-03-22"   # au format YYYY-MM-DD
date_end   = "2025-04-30"
# =============================================================================
# =============================================================================



# --- 2. Charger le GeoJSON et s'assurer du bon CRS ---
gdf = gpd.read_file(geojson_path)
if gdf.crs is not None and gdf.crs.to_epsg() != 4326:
    gdf = gdf.to_crs(4326)
minx, miny, maxx, maxy = gdf.total_bounds

# --- 3. Conversion des dates ---
starttime = datetime.fromisoformat(date_start)
endtime = datetime.fromisoformat(date_end)

# --- 4. Recherche des événements ---
events = search(
    minlongitude=minx,
    minlatitude=miny,
    maxlongitude=maxx,
    maxlatitude=maxy,
    starttime=starttime,
    endtime=endtime,
)

# --- 5. Afficher les attributs du premier événement pour inspecter ---
if events:
    first = events[0]
    print(first)
    print("----------- Attributs disponibles ----------")
    print(dir(first))
else:
    print("Aucun événement trouvé.")

# --- 6. Construire le DataFrame selon les attributs disponibles ---
# Liste possible des attributs à récupérer
cols = ["id", "time", "magnitude", "depth", "latitude", "longitude", "magtype", "gap", "rms", "horizontal_error", "vertical_error"]

data = []
for e in events:
    d = {}
    for c in cols:
        d[c] = getattr(e, c, None)
    data.append(d)
df = pd.DataFrame(data)
print(df.head())

# Tu pourras adapter la liste 'cols' en fonction de ce que tu vois dans le dir(first)


us6000q3p6 2025-03-24 04:38:32.700000 (29.189,93.747) 10.0 km M4.2
----------- Attributs disponibles ----------
['__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__getitem__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', '_jdict', 'alert', 'depth', 'getDetailEvent', 'getDetailURL', 'hasProduct', 'hasProperty', 'id', 'latitude', 'location', 'longitude', 'magnitude', 'properties', 'time', 'toDict', 'url']
           id                             time  magnitude  depth  latitude  \
0  us6000q3p6 2025-03-24 04:38:32.700000+00:00        4.2   10.0   29.1888   
1  us6000q3ny 2025-03-24 04:43:00.743000+00:00        4.1   10.0   29.2119   
2  us7000pm7w 2025-03-24 11:21:38.311000+00:00        5.0   10.0   28.1045   
3  us7000pmg7 

In [3]:
df = df.sort_values("magnitude", ascending=False)
df

id                             time  magnitude  depth  latitude  \
5   us7000pn9s 2025-03-28 06:20:52.715000+00:00        7.7   10.0   22.0110   
6   us7000pn9z 2025-03-28 06:32:04.777000+00:00        6.7   10.0   21.6975   
66  us6000q5ps 2025-04-13 02:24:57.717000+00:00        5.3   10.0   21.2292   
78  us7000pv6f 2025-04-26 04:21:49.088000+00:00        5.1   10.0   31.0900   
30  us7000pnkj 2025-03-29 09:20:48.229000+00:00        5.1   10.0   19.6858   
..         ...                              ...        ...    ...       ...   
64  us6000q5cs 2025-04-11 10:52:56.066000+00:00        4.1   10.0   24.0430   
59  us6000q575 2025-04-10 16:17:58.886000+00:00        3.9   10.0   21.7193   
56  us6000q4x4 2025-04-09 14:40:17.442000+00:00        3.6   10.0   21.4447   
57  us6000q4xc 2025-04-09 15:59:18.014000+00:00        3.6   10.0   21.9457   
49  us6000q3nd 2025-04-02 23:13:09.295000+00:00        3.5   10.0   21.9162   

    longitude magtype   gap   rms horizontal_error vertical_error  
5     95.9363    None  None  None             None           None  
6     95.9690    None  None  None             None           None  
66    96.0897    None  None  None             None           None  
78    98.9820    None  None  None             None           None  
30    96.0761    None  None  None             None           None  
..        ...     ...   ...   ...              ...            ...  
64    91.3615    None  None  None             None           None  
59    95.9475    None  None  None             None           None  
56    95.9352    None  None  None             None           None  
57    96.0058    None  None  None             None           None  
49    96.0733    None  None  None             None           None  

[84 rows x 11 columns]

## Création d'un geo df

In [4]:

import geopandas as gpd
from shapely.geometry import Point

gdf_map = gpd.GeoDataFrame(
    df,
    geometry=[Point(xy) for xy in zip(df.longitude, df.latitude)],
    crs="EPSG:4326"
)


In [13]:
# Export du GDF

gdf_map.to_file("seismes.gpkg", layer="seismes", driver="GPKG")


## Check sur une carte

In [5]:
# Load a map with data and config and height
from keplergl import KeplerGl
map_1 = KeplerGl(height=1000, show_docs=False)
map_1.add_data(data=df, name="Séismes")
map_1


# map_1.save_to_html(file_name="data_output/seismes_map.html")


KeplerGl(data={'Séismes': {'index': [5, 6, 66, 78, 30, 2, 77, 48, 8, 9, 7, 44, 61, 31, 43, 76, 68, 81, 47, 35,…

In [65]:
import folium
import numpy as np
from branca.colormap import linear

# Fonction pour rayon basé sur la magnitude
def mag_to_radius(mag):
    return 2 * np.exp(mag - 4)

# Définir l'échelle des magnitudes
min_mag = df["magnitude"].min()
max_mag = df["magnitude"].max()

# Création de la carte
m = folium.Map(location=[df["latitude"].mean(), df["longitude"].mean()], zoom_start=6, tiles="Cartodb dark_matter")

# Colormap jaune -> rouge
colormap = linear.YlOrRd_09.scale(min_mag, max_mag)
colormap.caption = "Magnitude"
colormap.add_to(m)

# Boucle sur les événements
for _, row in df.iterrows():
    mag = row["magnitude"]
    radius = mag_to_radius(mag) if mag else 2
    fill_color = colormap(mag) if mag else "#cccccc"

    folium.CircleMarker(
        location=[row["latitude"], row["longitude"]],
        radius=radius,
        popup=f"Mag {mag}<br>ID: {row['id']}",
        color="black",              # Bordure noire
        weight=1,                   # Épaisseur de la bordure
        fill=True,
        fill_color=fill_color,
        fill_opacity=0.6
    ).add_to(m)

m  # Affiche la carte dans le notebook


In [7]:
event_id = df.iloc[0]["id"]
print(event_id)  # Ex: 'us6000kikc'


us7000pn9s


### Accès à toutes les données de Shakemap

In [8]:
import requests
import json

event_id = "us7000pn9s"
url = f"https://earthquake.usgs.gov/fdsnws/event/1/query?eventid={event_id}&format=geojson"
r = requests.get(url)
data = r.json()
data

{'type': 'Feature',
 'properties': {'mag': 7.7,
  'place': '2025 Mandalay, Burma (Myanmar) Earthquake',
  'time': 1743142852715,
  'updated': 1751393086583,
  'tz': None,
  'url': 'https://earthquake.usgs.gov/earthquakes/eventpage/us7000pn9s',
  'felt': 2531,
  'cdi': 9.1,
  'mmi': 9.953,
  'alert': 'red',
  'status': 'reviewed',
  'tsunami': 0,
  'sig': 2910,
  'net': 'us',
  'code': '7000pn9s',
  'ids': ',us7000pn9s,usauto7000pn9s,pt25087002,at00sttln4,',
  'sources': ',us,usauto,pt,at,',
  'types': ',dyfi,earthquake-name,finite-fault,general-text,ground-failure,impact-text,internal-moment-tensor,internal-origin,losspager,moment-tensor,oaf,origin,phase-data,shakemap,',
  'nst': 246,
  'dmin': 3.474,
  'rms': 0.89,
  'gap': 24,
  'magType': 'mww',
  'type': 'earthquake',
  'title': 'M 7.7 - 2025 Mandalay, Burma (Myanmar) Earthquake',
  'products': {'dyfi': [{'indexid': '26646279',
     'indexTime': 1751393091187,
     'id': 'urn:usgs-product:us:dyfi:us7000pn9s:1751393086583',
     'ty

In [21]:
from datetime import datetime
properties = data.get("properties", {})
products = properties.get("products", {})

files = []

for product_type, product_list in products.items():
    for product in product_list:
        contents = product.get('contents', {})
        if isinstance(contents, dict):
            for file_name, file_info in contents.items():
                # Récupérer le timestamp s'il existe
                lastmod = file_info.get("lastModified")
                # Conversion si présent
                if lastmod is not None:
                    # lastmod est en millisecondes
                    lastmod_str = datetime.utcfromtimestamp(int(lastmod) / 1000).strftime('%Y-%m-%d %H:%M:%S')
                else:
                    lastmod_str = "unknown"
                files.append({
                    "product_type": product_type,
                    "file_name": file_name,
                    "url": file_info.get("url"),
                    "size": file_info.get("length", "unknown"),
                    "content_type": file_info.get("contentType", "unknown"),
                    "last_modified": lastmod_str
                })

files = sorted(files, key=lambda x: (x['product_type'], x['file_name']))

# Printing products

for f in files:
    print(
        f"{f['product_type']:16} {f['file_name']:40} "
        f"{f['size']:>10} bytes  {f['last_modified']:19}  {f['url']}"
    )

products_listing = []

for f in files:
    products_listing.append({
        "product_type": f["product_type"],
        "file_name": f["file_name"],
        "size": f["size"],
        "last_modified": f["last_modified"],
        "url": f["url"]
    })

df_product = pd.DataFrame(products_listing)

products_listing

dyfi             cdi_geo.txt                                   33462 bytes  2025-07-01 18:04:46  https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_geo.txt
dyfi             cdi_geo.xml                                  110595 bytes  2025-07-01 18:04:46  https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_geo.xml
dyfi             cdi_geo_1km.txt                              115242 bytes  2025-07-01 18:04:46  https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_geo_1km.txt
dyfi             cdi_zip.txt                                   23086 bytes  2025-07-01 18:04:46  https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_zip.txt
dyfi             cdi_zip.xml                                   48599 bytes  2025-07-01 18:04:46  https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_zip.xml
dyfi             contents.xml                                   4224 bytes  2025-07-01 18:04:46  https://e

/var/folders/8b/jbf_9gw94xs45f1kt0j8k5880000gq/T/ipykernel_29681/2675718706.py:17: DeprecationWarning: datetime.datetime.utcfromtimestamp() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.fromtimestamp(timestamp, datetime.UTC).
  lastmod_str = datetime.utcfromtimestamp(int(lastmod) / 1000).strftime('%Y-%m-%d %H:%M:%S')


[{'product_type': 'dyfi',
  'file_name': 'cdi_geo.txt',
  'size': 33462,
  'last_modified': '2025-07-01 18:04:46',
  'url': 'https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_geo.txt'},
 {'product_type': 'dyfi',
  'file_name': 'cdi_geo.xml',
  'size': 110595,
  'last_modified': '2025-07-01 18:04:46',
  'url': 'https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_geo.xml'},
 {'product_type': 'dyfi',
  'file_name': 'cdi_geo_1km.txt',
  'size': 115242,
  'last_modified': '2025-07-01 18:04:46',
  'url': 'https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_geo_1km.txt'},
 {'product_type': 'dyfi',
  'file_name': 'cdi_zip.txt',
  'size': 23086,
  'last_modified': '2025-07-01 18:04:46',
  'url': 'https://earthquake.usgs.gov/product/dyfi/us7000pn9s/us/1751393086583/cdi_zip.txt'},
 {'product_type': 'dyfi',
  'file_name': 'cdi_zip.xml',
  'size': 48599,
  'last_modified': '2025-07-01 18:04:46',
  'url': 'https://earthquake.usgs.gov/p

In [19]:
df_product.to_csv(f"data_output/products_id_{event_id}.csv")

In [20]:
df_product

product_type                  file_name      size        last_modified  \
0           dyfi                cdi_geo.txt     33462  2025-07-01 18:04:46   
1           dyfi                cdi_geo.xml    110595  2025-07-01 18:04:46   
2           dyfi            cdi_geo_1km.txt    115242  2025-07-01 18:04:46   
3           dyfi                cdi_zip.txt     23086  2025-07-01 18:04:46   
4           dyfi                cdi_zip.xml     48599  2025-07-01 18:04:46   
..           ...                        ...       ...                  ...   
176     shakemap  download/shake_result.hdf  31963388  2025-06-06 13:36:22   
177     shakemap      download/shakemap.kmz    831540  2025-06-06 13:36:22   
178     shakemap         download/shape.zip  26264669  2025-06-06 13:36:22   
179     shakemap  download/stationlist.json   3499574  2025-06-06 13:36:22   
180     shakemap   download/uncertainty.xml  18054674  2025-06-06 13:36:23   

                                                   url  
0    https://earthquake.usgs.gov/product/dyfi/us700...  
1    https://earthquake.usgs.gov/product/dyfi/us700...  
2    https://earthquake.usgs.gov/product/dyfi/us700...  
3    https://earthquake.usgs.gov/product/dyfi/us700...  
4    https://earthquake.usgs.gov/product/dyfi/us700...  
..                                                 ...  
176  https://earthquake.usgs.gov/product/shakemap/u...  
177  https://earthquake.usgs.gov/product/shakemap/u...  
178  https://earthquake.usgs.gov/product/shakemap/u...  
179  https://earthquake.usgs.gov/product/shakemap/u...  
180  https://earthquake.usgs.gov/product/shakemap/u...  

[181 rows x 5 columns]

## Get MMI shapefiles

In [22]:
import os
import requests
import zipfile
import geopandas as gpd
from glob import glob

# --- Paramètres ---
mmi_url = df_product[df_product["file_name"] == "download/shape.zip"]["url"].iloc[0]
base_dir = "data_output/shape_mmi"
os.makedirs(base_dir, exist_ok=True)
zip_path = os.path.join(base_dir, "mmi.zip")

# 1. Télécharger le ZIP
with requests.get(mmi_url, stream=True) as r:
    r.raise_for_status()
    with open(zip_path, "wb") as f:
        for chunk in r.iter_content(chunk_size=8192):
            f.write(chunk)

# 2. Extraire uniquement les .shp
with zipfile.ZipFile(zip_path, "r") as zip_ref:
    shp_members = [name for name in zip_ref.namelist() if name.endswith(".shp")]
    zip_ref.extractall(
        base_dir,
        members=shp_members
    )

# 3. Supprimer le ZIP
os.remove(zip_path)

# 4. Lister les .shp extraits
shp_files = []
for root, dirs, files in os.walk(base_dir):
    for file in files:
        if file.endswith(".shp"):
            rel_path = os.path.relpath(os.path.join(root, file), base_dir)
            shp_files.append(rel_path)

print("Shapefiles extraits :")
for path in shp_files:
    print("-", path)


Shapefiles extraits :
- psa3p0.shp
- psa1p0.shp
- psa0p3.shp
- pgv.shp
- pga.shp
- mi.shp


In [23]:

shp_path = os.path.join(base_dir, "mi.shp")

# Lecture du shapefile (les fichiers .shx, .dbf, .prj doivent être présents au même endroit)
gdf = gpd.read_file(shp_path)

# Aperçu attributs
print(gdf.head())

# Colonnes disponibles
print(gdf.columns)

# Exemple d'affichage d'une géométrie
print(gdf.geometry.iloc[0])

   AREA  PERIMETER  PGAPOL_  PGAPOL_ID  GRID_CODE  PARAMVALUE  \
0   NaN        NaN       14         14          0         2.8   
1   NaN        NaN       15         15          0         3.0   
2   NaN        NaN       16         16          0         3.2   
3   NaN        NaN       17         17          0         3.4   
4   NaN        NaN       18         18          0         3.6   

                                            geometry  
0  MULTIPOLYGON (((102.15192 26.75, 102.15032 26....  
1  MULTIPOLYGON (((101.22624 26.775, 101.22608 26...  
2  MULTIPOLYGON (((100.12571 26.775, 100.12539 26...  
3  MULTIPOLYGON (((97.07814 26.725, 97.07574 26.7...  
4  MULTIPOLYGON (((97.60229 26.725, 97.60131 26.7...  
Index(['AREA', 'PERIMETER', 'PGAPOL_', 'PGAPOL_ID', 'GRID_CODE', 'PARAMVALUE',
       'geometry'],
      dtype='object')
MULTIPOLYGON (((102.151915 26.75, 102.150315 26.749685, 102.15 26.746747, 102.149599 26.749599, 102.149697 26.75, 102.149849 26.750151, 102.15 26.75075, 102.1

In [24]:
gdf["PARAMVALUE_CLASS"] = gdf["PARAMVALUE"].astype(int)
import numpy as np
gdf["PARAMVALUE_CLASS"] = np.clip(gdf["PARAMVALUE"].astype(int), 0, int(gdf["PARAMVALUE"].max()))
gdf_dissolved = gdf.dissolve(by="PARAMVALUE_CLASS")


In [64]:
# gdf.explore(column="PARAMVALUE", cmap="OrRd", tiles="OpenStreetMap")
gdf_dissolved.explore(column="PARAMVALUE", cmap="OrRd", tiles="Cartodb dark_matter")


In [92]:
gdf_dissolved

geometry  AREA  \
PARAMVALUE_CLASS                                                            
2                 MULTIPOLYGON (((102.13081 13.03081, 102.125 13...   NaN   
3                 MULTIPOLYGON (((90.4 16.40328, 90.4 21.87164, ...   NaN   
4                 MULTIPOLYGON (((91.9 21.48347, 91.90848 21.483...   NaN   
5                 MULTIPOLYGON (((93.65579 18.80579, 93.65 18.80...   NaN   
6                 MULTIPOLYGON (((95.025 17.11756, 95.01865 17.1...   NaN   
7                 MULTIPOLYGON (((95.78991 17.63509, 95.79219 17...   NaN   
8                 MULTIPOLYGON (((96.53914 17.98914, 96.5349 17....   NaN   
9                 POLYGON ((96.44852 18.19852, 96.44723 18.2, 96...   NaN   
10                POLYGON ((95.975 22.36188, 95.97259 22.37259, ...   NaN   

                  PERIMETER  PGAPOL_  PGAPOL_ID  GRID_CODE  PARAMVALUE  
PARAMVALUE_CLASS                                                        
2                       NaN       14         14          0         2.8  
3                       NaN       15         15          0         3.0  
4                       NaN       20         20          0         4.0  
5                       NaN       25         25          0         5.0  
6                       NaN       30         30          0         6.0  
7                       NaN       35         35          0         7.0  
8                       NaN       40         40          0         8.0  
9                       NaN       45         45          0         9.0  
10                      NaN       50         50          0        10.0

## Access to product - function

In [31]:
# import URL

import requests

def get_json_data(df, pattern):
    """
    Recherche un fichier JSON contenant `pattern` dans son nom, le télécharge et retourne son contenu JSON.
    Erreur si 0 ou plusieurs fichiers trouvés.
    """
    mask = df['file_name'].str.contains(pattern, case=False, na=False) & df['file_name'].str.endswith('.json')
    matches = df[mask]
    if len(matches) == 0:
        raise ValueError(f"Aucun fichier JSON trouvé pour '{pattern}'")
    if len(matches) > 1:
        files = "\n".join(matches['file_name'])
        raise ValueError(f"Plusieurs fichiers trouvés pour '{pattern}':\n{files}\n=> Précise le pattern.")
    file_name = matches.iloc[0]['file_name']
    url = matches.iloc[0]['url']
    print(f"Téléchargement de : {file_name}")
    response = requests.get(url)
    response.raise_for_status()
    return response.json()



## Propreties

Detailed information on the earthquake

In [41]:
json_propreties = get_json_data(df_product, "properties")



📥 Téléchargement de : properties.json


In [46]:
# json_propreties
df_propreties = pd.DataFrame(list(json_propreties.items()), columns=["key", "value"])
df_propreties


key  \
0          average-rise-time   
1   average-rupture-velocity   
2              crustal-model   
3                      depth   
4          derived-magnitude   
5     derived-magnitude-type   
6                eventsource   
7            eventsourcecode   
8                  eventtime   
9               hypocenter-x   
10              hypocenter-z   
11                  latitude   
12                  location   
13                 longitude   
14         maximum-frequency   
15              maximum-rise   
16              maximum-slip   
17         minimum-frequency   
18                 model-dip   
19              model-length   
20              model-number   
21                model-rake   
22              model-strike   
23                 model-top   
24               model-width   
25          number-longwaves   
26             number-pwaves   
27            number-shwaves   
28             scalar-moment   
29             segment-1-dip   
30          segment-1-strike   
31             segment-2-dip   
32          segment-2-strike   
33             segment-3-dip   
34          segment-3-strike   
35             segment-4-dip   
36          segment-4-strike   
37                  segments   
38           subfault-1-area   
39         subfault-1-length   
40          subfault-1-width   
41           subfault-2-area   
42         subfault-2-length   
43          subfault-2-width   
44           subfault-3-area   
45         subfault-3-length   
46          subfault-3-width   
47           subfault-4-area   
48         subfault-4-length   
49          subfault-4-width   
50              time-windows   
51         velocity-function   
52                   version   

                                                value  
0                                                9.53  
1                                                3.88  
2   1D crustal model interpolated from CRUST2.0 (B...  
3                                                10.0  
4                                            7.695717  
5                                                  Mw  
6                                                  us  
7                                            7000pn9s  
8                         2025-03-28T00:00:00.000000Z  
9                                               115.0  
10                                              11.25  
11                                             22.013  
12          2025 Mandalay, Burma (Myanmar) Earthquake  
13                                               96.0  
14                                              0.125  
15                                               18.0  
16                                             4.3334  
17                                               0.01  
18                                               82.0  
19                                              200.0  
20                                                  1  
21                                             -175.0  
22                                              358.0  
23                                           1.087587  
24                                               22.5  
25                                                 61  
26                                                 34  
27                                                 44  
28                            440124653200000024576.0  
29                                               82.0  
30                                              358.0  
31                                               82.0  
32                                              355.0  
33                                               82.0  
34                                              352.0  
35                                               82.0  
36                                              350.0  
37                                                  4  
38                                        2313.630058  
39                                          150.46043  


### Cities

In [ ]:
json_cities = get_json_data(df_product, "cities")


📥 Téléchargement de : json/cities.json


{'all_cities': [{'name': 'Sagaing',
   'ccode': 'MM',
   'lat': 21.8787,
   'lon': 95.97965,
   'iscap': True,
   'pop': 78739,
   'mmi': 9.3805552535,
   'on_map': 0},
  {'name': 'Pyu',
   'ccode': 'MM',
   'lat': 18.4813,
   'lon': 96.43742,
   'iscap': False,
   'pop': 40386,
   'mmi': 9.2000003746,
   'on_map': 0},
  {'name': 'Yamethin',
   'ccode': 'MM',
   'lat': 20.43189,
   'lon': 96.13875,
   'iscap': False,
   'pop': 59867,
   'mmi': 9.1416668499,
   'on_map': 0},
  {'name': 'Pyinmana',
   'ccode': 'MM',
   'lat': 19.7381,
   'lon': 96.20742,
   'iscap': False,
   'pop': 97409,
   'mmi': 9.1166667915,
   'on_map': 0},
  {'name': 'Kyaukse',
   'ccode': 'MM',
   'lat': 21.6056,
   'lon': 96.13508,
   'iscap': False,
   'pop': 50480,
   'mmi': 8.9000001837,
   'on_map': 0},
  {'name': 'Nay Pyi Taw',
   'ccode': 'MM',
   'lat': 19.745,
   'lon': 96.12972,
   'iscap': True,
   'pop': 925000,
   'mmi': 8.8638888974,
   'on_map': 1},
  {'name': 'Yangon',
   'ccode': 'MM',
   'lat': 

In [55]:
df_cities = pd.DataFrame(json_cities['all_cities'])
df_cities

gdf_cities = gpd.GeoDataFrame(
    df_cities,
    geometry=[Point(xy) for xy in zip(df_cities['lon'], df_cities['lat'])],
    crs="EPSG:4326"  # WGS 84, coordonnées GPS standard
)

In [63]:
import matplotlib.pyplot as plt
import matplotlib


# Créer un color mapper
norm = plt.Normalize(vmin=gdf_cities['mmi'].min(), vmax=gdf_cities['mmi'].max())
cmap = plt.cm.get_cmap('YlOrRd')

def color_scale(mmi):
    rgba = cmap(norm(mmi))
    # Convertit en code couleur hex
    return matplotlib.colors.rgb2hex(rgba)

# Créer la carte
center = [gdf_cities['lat'].mean(), gdf_cities['lon'].mean()]
m = folium.Map(location=center, zoom_start=6, tiles="Cartodb dark_matter") # "CartoDB Positron"

# Ajouter les points
for _, row in gdf_cities.iterrows():
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=max(3, row['pop']**0.5 / 100),
        color=color_scale(row['mmi']),
        fill=True,
        fill_opacity=0.7,
        stroke=False,
        popup=folium.Popup(f"{row['name']}<br>Pop: {row['pop']}<br>MMI: {row['mmi']:.1f}", min_width=120)
    ).add_to(m)

m  # Affiche la carte dans le notebook


/var/folders/8b/jbf_9gw94xs45f1kt0j8k5880000gq/T/ipykernel_29681/263553277.py:7: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  cmap = plt.cm.get_cmap('YlOrRd')


### Exposure

In [66]:
json_exposure = get_json_data(df_product, "exposure")
json_exposure


📥 Téléchargement de : json/exposures.json


{'population_exposure': {'mmi': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
  'aggregated_exposure': [0,
   0,
   32989235,
   163708636,
   24656409,
   20277188,
   8787774,
   3636635,
   5800931,
   414753],
  'maximum_border_mmi': 4.099999904632569,
  'country_exposures': [{'country_code': 'BD',
    'exposure': [0, 0, 6739720, 68735336, 1953, 0, 0, 0, 0, 0]},
   {'country_code': 'BT', 'exposure': [0, 0, 381, 0, 0, 0, 0, 0, 0, 0]},
   {'country_code': 'MM',
    'exposure': [0,
     0,
     6815,
     5153110,
     13251671,
     20015152,
     8787774,
     3636635,
     6215684,
     414753]},
   {'country_code': 'KH',
    'exposure': [0, 0, 1735276, 17030, 0, 0, 0, 0, 0, 0]},
   {'country_code': 'CN',
    'exposure': [0, 0, 16166487, 16577580, 360732, 120558, 0, 0, 0, 0]},
   {'country_code': 'IN',
    'exposure': [0, 0, 531607, 36755560, 1448888, 0, 0, 0, 0, 0]},
   {'country_code': 'LA',
    'exposure': [0, 0, 1707388, 2212442, 0, 0, 0, 0, 0, 0]},
   {'country_code': 'VN', 'exposure': [0,

In [69]:
# Données principales
mmi = json_exposure['population_exposure']['mmi']

# Exposition totale par MMI
df_pop_agg = pd.DataFrame({
    'mmi': mmi,
    'pop_agg': json_exposure['population_exposure']['aggregated_exposure']
})

# Exposition par pays (long)
rows = []
for country in json_exposure['population_exposure']['country_exposures']:
    for m, exp in zip(mmi, country['exposure']):
        rows.append({
            'country': country['country_code'],
            'mmi': m,
            'pop_exposure': exp
        })
df_pop_countries = pd.DataFrame(rows)

# Un pivot pour format wide si tu veux
df_pop_countries_wide = df_pop_countries.pivot(index='country', columns='mmi', values='pop_exposure').reset_index()

df_pop_countries

country  mmi  pop_exposure
0       BD    1             0
1       BD    2             0
2       BD    3       6739720
3       BD    4      68735336
4       BD    5          1953
..     ...  ...           ...
85      TH    6        141478
86      TH    7             0
87      TH    8             0
88      TH    9             0
89      TH   10             0

[90 rows x 3 columns]

## Forecast

In [71]:
json_forecast = get_json_data(df_product, "forecast")
json_forecast


📥 Téléchargement de : forecast.json


{'creationTime': 1751302035274,
 'expireTime': 1782875639020,
 'advisoryTimeFrame': '1 Month',
 'template': 'Mainshock',
 'injectableText': 'This forecast is based on aftershocks recorded in the ANSS Comprehensive Earthquake Catalog (ComCat). More detailed earthquake information may be available from scientific agencies in the affected country.',
 'observations': [{'magnitude': 3.0, 'count': 78},
  {'magnitude': 5.0, 'count': 5},
  {'magnitude': 6.0, 'count': 1},
  {'magnitude': 7.0, 'count': 0}],
 'model': {'name': 'Epidemic-Type aftershock model (Bayesian Combination)',
  'reference': '#url',
  'parameters': {'ams': -2.85,
   'a': -2.5,
   'b': 1.04,
   'magMain': 7.7,
   'p': 0.9,
   'c': 0.0038,
   'Mc': 4.55,
   'regionType': 'circle',
   'regionCenterLat': 21.6962,
   'regionCenterLon': 95.9092,
   'regionRadius': 499.8}},
 'fractileProbabilities': [0.0025,
  0.005,
  0.0075,
  0.01,
  0.0125,
  0.015,
  0.0175,
  0.02,
  0.0225,
  0.025,
  0.0275,
  0.03,
  0.0325,
  0.035,
  0.

In [74]:
df_forecast = pd.DataFrame(json_forecast)


ValueError: All arrays must be of the same length

In [81]:
rows = []
for period in json_forecast["forecast"]:
    for bin_ in period["bins"]:
        row = {
            "timeStart": period["timeStart"],
            "timeEnd": period["timeEnd"],
            "label": period["label"],
            **bin_,  # ajoute magnitude, probability, etc.
        }
        rows.append(row)
df_bins = pd.DataFrame(rows)
print(df_bins.head())

df_bins["timeStart_dt"] = pd.to_datetime(df_bins["timeStart"], unit="ms")
df_bins["timeEnd_dt"] = pd.to_datetime(df_bins["timeEnd"], unit="ms")
df_bins


       timeStart        timeEnd  label  magnitude  p95minimum  p95maximum  \
0  1751310028715  1751396428715  1 Day        3.0           0           5   
1  1751310028715  1751396428715  1 Day        4.0           0           1   
2  1751310028715  1751396428715  1 Day        5.0           0           0   
3  1751310028715  1751396428715  1 Day        6.0           0           0   
4  1751310028715  1751396428715  1 Day        7.0           0           0   

   probability  median                                     fractileValues  \
0       0.7113       1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1       0.1135       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2       0.0106       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3       0.0003       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
4       0.0000       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                      barPercentages  
0  [29, 32, 36, 3, 0, 0, 0, 0, 0, 0

timeStart        timeEnd    label  magnitude  p95minimum  p95maximum  \
0   1751310028715  1751396428715    1 Day        3.0           0           5   
1   1751310028715  1751396428715    1 Day        4.0           0           1   
2   1751310028715  1751396428715    1 Day        5.0           0           0   
3   1751310028715  1751396428715    1 Day        6.0           0           0   
4   1751310028715  1751396428715    1 Day        7.0           0           0   
5   1751310028715  1751914828715   1 Week        3.0           2          23   
6   1751310028715  1751914828715   1 Week        4.0           0           4   
7   1751310028715  1751914828715   1 Week        5.0           0           1   
8   1751310028715  1751914828715   1 Week        6.0           0           0   
9   1751310028715  1751914828715   1 Week        7.0           0           0   
10  1751310028715  1753988428715  1 Month        3.0          16          94   
11  1751310028715  1753988428715  1 Month        4.0           0          11   
12  1751310028715  1753988428715  1 Month        5.0           0           2   
13  1751310028715  1753988428715  1 Month        6.0           0           1   
14  1751310028715  1753988428715  1 Month        7.0           0           0   
15  1751310028715  1782932428715   1 Year        3.0         105         872   
16  1751310028715  1782932428715   1 Year        4.0           8          82   
17  1751310028715  1782932428715   1 Year        5.0           0          10   
18  1751310028715  1782932428715   1 Year        6.0           0           2   
19  1751310028715  1782932428715   1 Year        7.0           0           0   

    probability  median                                     fractileValues  \
0        0.7113       1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1        0.1135       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2        0.0106       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3        0.0003       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
4        0.0000       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
5        0.9985       9  [1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 3, 3, 3, 3, 3, ...   
6        0.5596       1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
7        0.0738       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
8        0.0074       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
9        0.0006       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
10       0.9999      40  [10, 12, 13, 13, 14, 14, 15, 15, 16, 16, 16, 1...   
11       0.9490       3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
12       0.2751       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
13       0.0310       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
14       0.0026       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
15       0.9999     267  [68, 78, 83, 87, 90, 94, 97, 100, 102, 105, 10...   
16       0.9999      24  [4, 5, 5, 6, 6, 6, 7, 7, 7, 8, 8, 8, 8, 8, 9, ...   
17       0.8391       2  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
18       0.1885       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
19       0.0201       0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                        barPercentages            timeStart_dt  \
0    [29, 32, 36, 3, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
1     [89, 10, 1, 0, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
2      [99, 1, 0, 0, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
3     [100, 0, 0, 0, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
4     [100, 0, 0, 0, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
5    [0, 1, 11, 40, 43, 5, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
6    [44, 33, 22, 1, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
7      [93, 7, 1, 0, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
8      [99, 1, 0, 0, 0, 0, 0, 0, 0, 0] 2025-06-30 19:00:28.715   
9     [100, 0, 0, 0, 0, 0, 0